# Gesture Annotation Notebook |

##### <strong>Author:</strong> <u>Walter Dych</u> <em>(walterpdych@gmail.com)</em>
##### <strong>Edits/Documentation:</strong> <u>Karee Garvin</u> <em>(kgarvin@fas.harvard.edu)</em>

In [22]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

In [23]:
data = pd.read_csv('C:/Users/cosmo/Desktop/Random Scripts/Co-Speech Gesture Automation/Co-Speech-Gesture-Automation/SPEED_FILES/5003_I_right_wrist_processed_data.csv')
data.head()

right_shoulder_x  right_shoulder_y  left_shoulder_x  left_shoulder_y  \
0          0.199463          0.340649         0.307089         0.326427   
1          0.199377          0.340663         0.307126         0.325872   
2          0.199291          0.340676         0.307163         0.325316   
3          0.199205          0.340690         0.307200         0.324761   
4          0.199069          0.340718         0.307221         0.324481   

   right_elbow_x  right_elbow_y  left_elbow_x  left_elbow_y  right_wrist_x  \
0       0.209208       0.516104      0.317789      0.469892       0.309411   
1       0.209409       0.516585      0.317781      0.469893       0.309574   
2       0.209610       0.517066      0.317773      0.469894       0.309738   
3       0.209811       0.517547      0.317766      0.469894       0.309902   
4       0.209953       0.517743      0.317766      0.469922       0.310107   

   right_wrist_y  ...  left_wrist_y  right_eye_x  right_eye_y  left_eye_x  \
0       0.596308  ...      0.567451     0.261056     0.208618    0.284653   
1       0.597081  ...      0.568346     0.263065     0.209292    0.284846   
2       0.597854  ...      0.569241     0.265075     0.209966    0.285039   
3       0.598627  ...      0.570136     0.267084     0.210641    0.285232   
4       0.599156  ...      0.570758     0.267888     0.211044    0.285349   

   left_eye_y    nose_x    nose_y  speed_unsmooth  speed_smooth  time_ms  
0    0.215582  0.278071  0.237287             NaN           NaN      0.0  
1    0.215597  0.279773  0.237189             NaN           NaN     10.0  
2    0.215611  0.281476  0.237091             NaN           NaN     20.0  
3    0.215626  0.283179  0.236994        0.071042           NaN     30.0  
4    0.215656  0.283793  0.236955        0.064357           NaN     40.0  

[5 rows x 21 columns]

In [24]:
MAX_S_LENGTH = 100
MAX_STEADY_LENGTH = 100
THRESHOLD = 0.4
COLORS = {'Stroke': 'rgba(231,107,243,0.2)', 'Rest': 'rgba(107,174,214,0.2)', '': 'rgba(255,255,255,0.2)'}

In [25]:
def generate_annotations(data): # Generate annotations based on speed_smooth data.
    speed_smooth = list(map(float, data['speed_smooth']))
    phase = [''] * len(speed_smooth)
    last_stroke_type = None
    start_index = None
    steady_start = None
    steady_end = None
    apexes = [''] * len(speed_smooth)

    # Iterate over the speed_smooth array to generate the annotations
    for i in range(1, len(speed_smooth)):
        if speed_smooth[i] > THRESHOLD and speed_smooth[i-1] <= THRESHOLD:
            if last_stroke_type is None or last_stroke_type == 'Steady' or last_stroke_type == 'R':
                last_stroke_type = 'Approach'
                start_index = i
            elif last_stroke_type == 'Approach' and i - start_index >= MAX_S_LENGTH:
                last_stroke_type = None
        elif speed_smooth[i] <= THRESHOLD and speed_smooth[i-1] > THRESHOLD:
            if last_stroke_type == 'Approach':
                last_stroke_type = 'Steady'
                start_index = i
                steady_start = i
            elif last_stroke_type == 'R':
                last_stroke_type = None
                start_index = None
        elif last_stroke_type == 'Steady' and speed_smooth[i] > THRESHOLD and speed_smooth[i-1] <= THRESHOLD:
            if steady_end is not None:
                last_stroke_type = 'R'
                start_index = i

        if last_stroke_type == 'Steady' and steady_start is None:
            steady_start = i
        elif steady_start is not None and last_stroke_type != 'Steady':
            steady_end = i
            min_speed_index = np.argmin(speed_smooth[steady_start:i]) + steady_start
            apexes[min_speed_index] = 'AX'
            steady_start = None
            if speed_smooth[i] > THRESHOLD and speed_smooth[i-1] <= THRESHOLD:
                last_stroke_type = 'R'
                start_index = i
        elif last_stroke_type == 'Steady' and i - start_index >= MAX_STEADY_LENGTH:
            last_stroke_type = None
            start_index = None
            steady_start = None
        phase[i] = last_stroke_type if last_stroke_type is not None else ''

    data = pd.DataFrame({
        'time_ms': data['time_ms'],
        'speed_unsmooth': data['speed_unsmooth'],
        'speed_smooth': data['speed_smooth'],
        'phase': phase, 
        'apex': apexes
    })

    data['phase'] = data['phase'].apply(lambda x: 'Stroke' if x in ['Steady', 'Approach'] else ('Rest' if x == 'R' else ''))
    return data



In [26]:
data = generate_annotations(data)
data.head()

time_ms  speed_unsmooth  speed_smooth phase apex
0      0.0             NaN           NaN           
1     10.0             NaN           NaN           
2     20.0             NaN           NaN           
3     30.0        0.071042           NaN           
4     40.0        0.064357           NaN

In [27]:
data.to_csv('C:/Users/cosmo/Desktop/Random Scripts/Co-Speech Gesture Automation/Co-Speech-Gesture-Automation/ANNOTATIONS/5003_I_right_wrist_annotations.csv', index=False)

In [28]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=data['time_ms'], 
    y=data['speed_smooth'], 
    mode='lines',
    name='Speed curve'
))

data['phase_change'] = data['phase'].shift() != data['phase']
data['Group'] = data['phase_change'].cumsum()
interval_df = data.groupby(['Group', 'phase']).agg(Start=('time_ms', 'min'), End=('time_ms', 'max')).reset_index()

shapes = []
for _, row in interval_df.iterrows():
    shapes.append(dict(
        type="rect",
        xref="x", yref="paper",
        x0=row['Start'], x1=row['End'],
        y0=0, y1=1,
        fillcolor=COLORS[row['phase']],
        opacity=0.85,
        layer="below",
        line_width=0,
    ))

for phase in COLORS.keys():
    fig.add_trace(go.Scatter(
        x=[None], y=[None],
        mode='markers',
        marker=dict(size=15, color=COLORS[phase]),
        showlegend=True,
        name=phase,
    ))

apex_df = data[data['apex'] == 'AX']
fig.add_trace(go.Scatter(
    x=apex_df['time_ms'], 
    y=apex_df['speed_smooth'], 
    mode='markers',
    name='Apexes'
))

fig.update_xaxes(title_text='Time (ms)')
fig.update_yaxes(title_text='Speed (px/ms)')
fig.update_layout(showlegend=True, shapes=shapes)
fig.update_layout(title_text='Smoothed Speed Curve with Annotations')
fig.update_layout(width=1250, height=750)
fig.show()
